In [124]:
#conda update numpy

In [125]:
#conda install -c conda-forge catboost xgboost

In [126]:
'''
try:
    from catboost import CatBoostRegressor
    from xgboost import XGBRegressor
    print("CatBoost and XGBoost imported successfully.")
except Exception as e:
    print(f"Error: {e}")
'''

'\ntry:\n    from catboost import CatBoostRegressor\n    from xgboost import XGBRegressor\n    print("CatBoost and XGBoost imported successfully.")\nexcept Exception as e:\n    print(f"Error: {e}")\n'

In [127]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt 

from sklearn.model_selection import train_test_split
from sklearn.neighbors import KNeighborsRegressor
from sklearn.tree import DecisionTreeRegressor
from sklearn.ensemble import RandomForestRegressor,AdaBoostRegressor
from sklearn.svm import SVR
from sklearn.linear_model import LinearRegression, Ridge,Lasso
from sklearn.metrics import r2_score, mean_absolute_error, mean_squared_error
from catboost import CatBoostRegressor
from xgboost import XGBRegressor
import warnings

In [128]:
df = pd.read_csv('data/StudentsPerformance.csv')
df.head()

gender race/ethnicity parental level of education         lunch  \
0  female        group B           bachelor's degree      standard   
1  female        group C                some college      standard   
2  female        group B             master's degree      standard   
3    male        group A          associate's degree  free/reduced   
4    male        group C                some college      standard   

  test preparation course  math score  reading score  writing score  
0                    none          72             72             74  
1               completed          69             90             88  
2                    none          90             95             93  
3                    none          47             57             44  
4                    none          76             78             75

In [129]:
X = df.drop(columns=['math score'],axis=1)
y = df['math score']

In [131]:
# trnasform the categorical data into numerical data use onehotcoder and columntransformer
from sklearn.preprocessing import OneHotEncoder, StandardScaler
from sklearn.compose import make_column_transformer

y = df['math score']  
X = df.drop('math score', axis=1)


categorical_cols = X.select_dtypes(include=['object']).columns
numeric_cols = X.select_dtypes(include=['float64', 'int64']).columns

preprocessor = make_column_transformer(
    (OneHotEncoder(sparse=False, handle_unknown='ignore'), categorical_cols),
    (StandardScaler(), numeric_cols)
)


X_transformed = preprocessor.fit_transform(X)

/Users/Peizhi/miniconda3/envs/myenv/lib/python3.11/site-packages/sklearn/preprocessing/_encoders.py:975: FutureWarning: `sparse` was renamed to `sparse_output` in version 1.2 and will be removed in 1.4. `sparse_output` is ignored unless you leave `sparse` to its default value.
  warnings.warn(


In [155]:
X_train, X_test, y_train, y_test = train_test_split(X_transformed, y, test_size=0.2, random_state=42)

In [156]:
X_train.shape, X_test.shape, y_train.shape, y_test.shape

((800, 19), (200, 19), (800,), (200,))

In [161]:
from sklearn.model_selection import cross_val_score

# Create a dictionary of models
models = {
    'KNeighborsRegressor': KNeighborsRegressor(),
    'DecisionTreeRegressor': DecisionTreeRegressor(),
    'RandomForestRegressor': RandomForestRegressor(),
    'AdaBoostRegressor': AdaBoostRegressor(),
    'SVR': SVR(),
    'LinearRegression': LinearRegression(),
    'Ridge': Ridge(),
    'Lasso': Lasso(),
    'CatBoost': CatBoostRegressor(),
    'XGBoost': XGBRegressor()
}

model_list = []

# Loop through the models
for model_name, model in models.items():
    mse = cross_val_score(model, X_train, y_train, cv=5, scoring='neg_mean_squared_error').mean()
    mse = np.sqrt(-mse)
    mae = cross_val_score(model, X_train, y_train, cv=5, scoring='neg_mean_absolute_error').mean()
    mae = -mae
    r2 = cross_val_score(model, X_train, y_train, cv=5, scoring='r2').mean()
    model_list.append({ 'model': model_name, 'mse': mse, 'mae': mae, 'r2': r2 })
    
# Print the model_list
for model in model_list:
    print(model['model'])
    print(f'R2 Score: {model["r2"]}')
    print(f'Mean Absolute Error: {model["mae"]}')
    print(f'Mean Squared Error: {model["mse"]}')
    print('\n')

Learning rate set to 0.038155
0:	learn: 14.4355373	total: 6.93ms	remaining: 6.92s
1:	learn: 14.1347681	total: 7.33ms	remaining: 3.66s
2:	learn: 13.7912381	total: 7.67ms	remaining: 2.55s
3:	learn: 13.4624652	total: 12ms	remaining: 2.98s
4:	learn: 13.1329105	total: 12.7ms	remaining: 2.52s
5:	learn: 12.8671007	total: 13.4ms	remaining: 2.21s
6:	learn: 12.5787664	total: 13.8ms	remaining: 1.95s
7:	learn: 12.3289514	total: 14.1ms	remaining: 1.75s
8:	learn: 12.0816829	total: 14.7ms	remaining: 1.62s
9:	learn: 11.8077460	total: 15ms	remaining: 1.48s
10:	learn: 11.5458640	total: 15.3ms	remaining: 1.38s
11:	learn: 11.3240956	total: 15.7ms	remaining: 1.29s
12:	learn: 11.0908608	total: 17.3ms	remaining: 1.31s
13:	learn: 10.8854420	total: 17.7ms	remaining: 1.24s
14:	learn: 10.6563962	total: 18ms	remaining: 1.18s
15:	learn: 10.4639246	total: 18.3ms	remaining: 1.13s
16:	learn: 10.2660999	total: 18.7ms	remaining: 1.08s
17:	learn: 10.0833808	total: 19ms	remaining: 1.04s
18:	learn: 9.9034823	total: 19.3ms

In [162]:
# Create a dataframe using models' names and their scores
scores_df = pd.DataFrame(model_list)
scores_df

model       mse       mae        r2
0    KNeighborsRegressor  7.162699  5.690250  0.771319
1  DecisionTreeRegressor  8.120133  6.648125  0.697206
2  RandomForestRegressor  6.125807  4.917901  0.834656
3      AdaBoostRegressor  6.307431  5.069799  0.822150
4                    SVR  7.208049  5.430791  0.769624
5       LinearRegression  5.463262  4.379209  0.867053
6                  Ridge  5.429966  4.359388  0.868607
7                  Lasso  6.619543  5.224446  0.805300
8               CatBoost  5.908021  4.773501  0.844169
9                XGBoost  6.613308  5.306552  0.805269

In [163]:
from sklearn.ensemble import StackingRegressor


# Create a list of tuples containing the model name and the corresponding model object
estimators = [
    ('RandomForestRegressor', RandomForestRegressor()),
    ('AdaBoostRegressor', AdaBoostRegressor()),
    ('LinearRegression', LinearRegression()),
    ('Ridge', Ridge()),
    ('CatBoost', CatBoostRegressor())
]

# Create the stacking ensemble model
stacking_model = StackingRegressor(estimators=estimators, final_estimator=LinearRegression())

# Fit the stacking model on the training data
mse = cross_val_score(stacking_model, X_train, y_train, cv=5, scoring='neg_mean_squared_error').mean()
mse = np.sqrt(-mse)
mae = cross_val_score(stacking_model, X_train, y_train, cv=5, scoring='neg_mean_absolute_error').mean()
mae = -mae
r2 = cross_val_score(stacking_model, X_train, y_train, cv=5, scoring='r2').mean()
print(f'R2 Score: {r2:.2f}')
print(f'Mean Absolute Error: {mae:.2f}')
print(f'Mean Squared Error: {mse:.2f}')


Learning rate set to 0.038155
0:	learn: 14.4355373	total: 747us	remaining: 746ms
1:	learn: 14.1347681	total: 1.25ms	remaining: 623ms
2:	learn: 13.7912381	total: 1.96ms	remaining: 650ms
3:	learn: 13.4624652	total: 2.38ms	remaining: 593ms
4:	learn: 13.1329105	total: 2.77ms	remaining: 552ms
5:	learn: 12.8671007	total: 3.15ms	remaining: 522ms
6:	learn: 12.5787664	total: 3.55ms	remaining: 503ms
7:	learn: 12.3289514	total: 3.99ms	remaining: 495ms
8:	learn: 12.0816829	total: 4.36ms	remaining: 480ms
9:	learn: 11.8077460	total: 4.57ms	remaining: 453ms
10:	learn: 11.5458640	total: 4.92ms	remaining: 442ms
11:	learn: 11.3240956	total: 5.24ms	remaining: 431ms
12:	learn: 11.0908608	total: 6.45ms	remaining: 490ms
13:	learn: 10.8854420	total: 6.86ms	remaining: 483ms
14:	learn: 10.6563962	total: 7.25ms	remaining: 476ms
15:	learn: 10.4639246	total: 7.72ms	remaining: 475ms
16:	learn: 10.2660999	total: 8.14ms	remaining: 471ms
17:	learn: 10.0833808	total: 8.51ms	remaining: 464ms
18:	learn: 9.9034823	total:

In [164]:
stacking_model.fit(X_train, y_train)

y_pred = stacking_model.predict(X_test)


final_r2 = r2_score(y_test, y_pred)
final_mae = mean_absolute_error(y_test, y_pred)
final_mse = mean_squared_error(y_test, y_pred)

print(f'Final R2 Score: {final_r2:.2f}')
print(f'Final Mean Absolute Error: {final_mae:.2f}')
print(f'Final Mean Squared Error: {final_mse:.2f}')

Learning rate set to 0.039525
0:	learn: 14.5987177	total: 1.66ms	remaining: 1.66s
1:	learn: 14.2251886	total: 2.15ms	remaining: 1.07s
2:	learn: 13.8866124	total: 2.62ms	remaining: 872ms
3:	learn: 13.5235688	total: 3.08ms	remaining: 766ms
4:	learn: 13.1887021	total: 3.62ms	remaining: 720ms
5:	learn: 12.9124226	total: 4.01ms	remaining: 665ms
6:	learn: 12.6000335	total: 4.4ms	remaining: 625ms
7:	learn: 12.3299057	total: 4.79ms	remaining: 594ms
8:	learn: 12.0660619	total: 5.16ms	remaining: 568ms
9:	learn: 11.7730981	total: 5.67ms	remaining: 561ms
10:	learn: 11.4922764	total: 6ms	remaining: 539ms
11:	learn: 11.2626483	total: 6.33ms	remaining: 521ms
12:	learn: 11.0426039	total: 6.7ms	remaining: 509ms
13:	learn: 10.7991693	total: 7.13ms	remaining: 502ms
14:	learn: 10.5541002	total: 7.46ms	remaining: 490ms
15:	learn: 10.3191811	total: 7.8ms	remaining: 480ms
16:	learn: 10.1000444	total: 8.19ms	remaining: 473ms
17:	learn: 9.8945567	total: 8.51ms	remaining: 464ms
18:	learn: 9.6901741	total: 8.84m